In [87]:
import pandas as pd
import json
import re

Place-Recording Cleaning/Binary Encoding

In [93]:
df = pd.read_parquet('place_recording_relationships.parquet')

In [94]:
df

place_id  \
0      f9a1fd95-4c6d-43a6-bb31-4ee8d5a44a8b   
1      6ff650ca-94ed-4119-8123-b113f9cc9957   
2      d0000ec2-2343-415b-ba58-6c14d0b8007e   
3      42e9fa7c-a981-44f9-943c-bf39a8c6ce8d   
4      34e7351d-715d-4b20-a5d6-3c0bd717eb1d   
...                                     ...   
62859  6b94062e-78a3-46e8-b861-d801dfe27376   
62860  5ffbe933-6531-486a-91ea-553ee9036cd8   
62861  f7362574-05ac-4c21-8196-26a09d6e5fe7   
62862  6bd7adb1-b8dd-4ee5-bbe8-788444556350   
62863  9558b3a1-4eb8-4e45-8397-aadb54e572b4   

                                           relationships  
0      "\"\\\"\\\\\\\"[{\\\\\\\\\\\\\\\"type\\\\\\\\\...  
1      "\"\\\"\\\\\\\"[{\\\\\\\\\\\\\\\"type\\\\\\\\\...  
2      "\"\\\"\\\\\\\"[{\\\\\\\\\\\\\\\"type\\\\\\\\\...  
3      "\"\\\"\\\\\\\"[{\\\\\\\\\\\\\\\"type\\\\\\\\\...  
4      "\"\\\"\\\\\\\"[{\\\\\\\\\\\\\\\"type\\\\\\\\\...  
...                                                  ...  
62859                                                 []  
62860  [{"type": "recorded at", "recording": {"title"...  
62861                                                 []  
62862                                                 []  
62863                                                 []  

[62864 rows x 2 columns]

In [95]:
target_relationships = [
    "arranged at",
    "engineered at",
    "recorded at",
    "mixed at",
    "edited at",
    "remixed at",
    "produced at",
    "video shot at",
]

In [96]:
def clean_json_string(json_str):
    """Cleans and fixes escaped JSON strings."""
    try:
        cleaned_str = json_str.encode().decode("unicode_escape")
        cleaned_str = cleaned_str.strip('"')
        return cleaned_str
    except Exception as e:
        print(f"Error cleaning JSON string: {e}")
        return None

In [97]:
def extract_relationships_values(rel_str):
    """Extracts relevant relationships as dictionary objects."""
    try:
        if not isinstance(rel_str, str) or rel_str.strip() == "":
            return pd.Series({rel_type: None for rel_type in target_relationships})

        cleaned_str = clean_json_string(rel_str)

        relationships = json.loads(cleaned_str)

        if not isinstance(relationships, list):
            return pd.Series({rel_type: None for rel_type in target_relationships})

        rel_dict = {rel_type: None for rel_type in target_relationships}

        for entry in relationships:
            rel_type = entry.get("type", "").strip().lower()
            if rel_type in rel_dict:
                rel_dict[rel_type] = entry

        return pd.Series(rel_dict)

    except json.JSONDecodeError as e:
        print(f"JSON parsing error: {e}\nOffending string: {rel_str[:500]}")
        return pd.Series({rel_type: None for rel_type in target_relationships})
    except Exception as e:
        print(f"General error processing: {rel_str[:500]} -> {e}")
        return pd.Series({rel_type: None for rel_type in target_relationships})

In [98]:
df_extracted_values = df["relationships"].apply(extract_relationships_values)

JSON parsing error: Expecting value: line 1 column 1 (char 0)
Offending string: "\"\\\"\\\\\\\"[{\\\\\\\\\\\\\\\"type\\\\\\\\\\\\\\\": \\\\\\\\\\\\\\\"engineered at\\\\\\\\\\\\\\\", \\\\\\\\\\\\\\\"recording\\\\\\\\\\\\\\\": {\\\\\\\\\\\\\\\"disambiguation\\\\\\\\\\\\\\\": \\\\\\\\\\\\\\\"\\\\\\\\\\\\\\\", \\\\\\\\\\\\\\\"id\\\\\\\\\\\\\\\": \\\\\\\\\\\\\\\"99269b46-c5b2-4575-9677-2eb7dbe09f82\\\\\\\\\\\\\\\", \\\\\\\\\\\\\\\"video\\\\\\\\\\\\\\\": false, \\\\\\\\\\\\\\\"length\\\\\\\\\\\\\\\": 193000, \\\\\\\\\\\\\\\"title\\\\\\\\\\\\\\\": \\\\\\\\\\\\\\\"Capt. St. Lucifer
JSON parsing error: Expecting value: line 1 column 1 (char 0)
Offending string: "\"\\\"\\\\\\\"[{\\\\\\\\\\\\\\\"type\\\\\\\\\\\\\\\": \\\\\\\\\\\\\\\"engineered at\\\\\\\\\\\\\\\", \\\\\\\\\\\\\\\"recording\\\\\\\\\\\\\\\": {\\\\\\\\\\\\\\\"length\\\\\\\\\\\\\\\": 141000, \\\\\\\\\\\\\\\"id\\\\\\\\\\\\\\\": \\\\\\\\\\\\\\\"8ffd7c0b-4513-4312-a1d7-396992ecf1c4\\\\\\\\\\\\\\\", \\\\\\\\\\\\\\\"video\\\\\\\\\\\\\\\": 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



JSON parsing error: Expecting property name enclosed in double quotes: line 1 column 3 (char 2)
Offending string: "\"[{\\\"type\\\": \\\"recorded at\\\", \\\"recording\\\": {\\\"disambiguation\\\": \\\"\\\", \\\"id\\\": \\\"6a9305de-1345-4978-ae72-8bcb7c258832\\\", \\\"video\\\": false, \\\"length\\\": 278622, \\\"title\\\": \\\"Genocide City\\\"}}]\""
JSON parsing error: Expecting property name enclosed in double quotes: line 1 column 3 (char 2)
Offending string: "\"[{\\\"type\\\": \\\"recorded at\\\", \\\"recording\\\": {\\\"title\\\": \\\"Iron Cloud\\\", \\\"video\\\": false, \\\"length\\\": 249861, \\\"id\\\": \\\"cab48921-b224-4b29-8fc3-eaa4f0853a8e\\\", \\\"disambiguation\\\": \\\"\\\"}}]\""
JSON parsing error: Expecting property name enclosed in double quotes: line 1 column 3 (char 2)
Offending string: "\"[{\\\"type\\\": \\\"recorded at\\\", \\\"recording\\\": {\\\"video\\\": false, \\\"length\\\": 246800, \\\"title\\\": \\\"The Model\\\", \\\"disambiguation\\\": \\\"live, 1981-

In [99]:
df_values_only = pd.concat([df[["place_id"]], df_extracted_values], axis=1)

In [108]:
value_counts = df_values_only.count().reset_index()
value_counts.columns = ['Column Name', 'Count']
value_counts

Column Name  Count
0       place_id  62864
1    arranged at     52
2  engineered at   1109
3    recorded at  11371
4       mixed at   3209
5      edited at    271
6     remixed at     34
7    produced at    253
8  video shot at    103

In [109]:
def binary_encode_relationships(rel_series):
    """Converts extracted relationship values to binary encoding."""
    return rel_series.notna().astype(int)

In [110]:
df_binary_encoded = df_extracted_values.apply(binary_encode_relationships)

In [111]:
df_final_binary = pd.concat([df[["place_id"]], df_binary_encoded], axis=1)


In [114]:
df_final_binary.to_csv('place_recording_relationships.csv')

Place-work Cleaning/Binary Encoding

In [236]:
df = pd.read_parquet('place_work_relationships.parquet')

In [237]:
df['relationships'].value_counts()

relationships
"\"[]\""                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  

In [238]:
target_relationships_work = [
    "premiere",
    "written at",
    "composed at",
    "lyrics written at",
    "libretto written at",
    "revised at",
    "translated at",
    "arranged at",
    "commissioned",
    "dedication"
]

In [239]:
def fix_json_format(json_str):
    """Cleans and fixes JSON format before parsing."""
    try:
        if not isinstance(json_str, str) or json_str.strip() == "":
            return []

        cleaned_str = json_str.replace('\\"', '"')
        cleaned_str = cleaned_str.strip('"')
        cleaned_str = re.sub(r'\\+', r'\\', cleaned_str)

        return json.loads(cleaned_str)

    except json.JSONDecodeError as e:
        print(f"JSON parsing error: {e}\nOffending string: {json_str[:500]}")
        return []
    except Exception as e:
        print(f"General error processing JSON: {e}\nOffending string: {json_str[:500]}")
        return []

In [1]:
def extract_work_relationships(rel_str):

    """Extracts relevant work relationships, ensuring only relevant values are assigned and using None for empty fields."""

    try:
        if not isinstance(rel_str, str) or rel_str.strip() == "":
            return pd.Series({rel_type: None for rel_type in target_relationships_work})

        relationships = fix_json_format(rel_str)
        if not isinstance(relationships, list):
            return pd.Series({rel_type: None for rel_type in target_relationships_work})

        rel_dict = {rel_type: None for rel_type in target_relationships_work}
        for entry in relationships:
            rel_type = entry.get("type", "").strip().lower()
            work_info = entry.get("work", {}).get("title")
            if rel_type in rel_dict and work_info:
                rel_dict[rel_type] = work_info

        for key in rel_dict.keys():
            if isinstance(rel_dict[key], list) and not rel_dict[key]:
                rel_dict[key] = None

        return pd.Series(rel_dict)

    except Exception as e:
        print(f"General error processing: {rel_str[:500]} -> {e}")
        return pd.Series({rel_type: None for rel_type in target_relationships_work})

In [241]:
df_work_extracted_values = df["relationships"].apply(extract_work_relationships)


JSON parsing error: Expecting property name enclosed in double quotes: line 1 column 3 (char 2)
Offending string: "\"[{\\\"ended\\\": true, \\\"type\\\": \\\"premiere\\\", \\\"attribute-values\\\": {}, \\\"attributes\\\": [], \\\"attribute-ids\\\": {}, \\\"target-credit\\\": \\\"\\\", \\\"direction\\\": \\\"forward\\\", \\\"begin\\\": \\\"1940-11-07\\\", \\\"type-id\\\": \\\"a4d2a7cb-365b-4b90-b52f-29469edf8ac0\\\", \\\"target-type\\\": \\\"work\\\", \\\"work\\\": {\\\"id\\\": \\\"5acb0fcc-1c85-4b0e-9d1f-eb0809593056\\\", \\\"disambiguation\\\": \\\"\\\", \\\"language\\\": \\\"zxx\\\", \\\"iswcs\\\": [], \\
JSON parsing error: Expecting property name enclosed in double quotes: line 1 column 3 (char 2)
Offending string: "\"[{\\\"target-credit\\\": \\\"\\\", \\\"work\\\": {\\\"type-id\\\": null, \\\"language\\\": null, \\\"iswcs\\\": [], \\\"languages\\\": [], \\\"attributes\\\": [], \\\"title\\\": \\\"Divo Aloysio Sacrum\\\", \\\"type\\\": null, \\\"id\\\": \\\"81209428-d76a-425c-9841-8

In [242]:
df_work_values_only = pd.concat([df[["place_id"]], df_work_extracted_values], axis=1)


In [243]:
value_counts = df_work_values_only.count().reset_index()
value_counts.columns = ['Column Name', 'Count']
value_counts

Column Name  Count
0              place_id  62864
1              premiere  62864
2            written at  62864
3           composed at  62864
4     lyrics written at  62864
5   libretto written at  62864
6            revised at  62864
7         translated at  62864
8           arranged at  62864
9          commissioned  62864
10           dedication  62864

In [244]:
df_work_values_only

place_id premiere written at composed at  \
0      f9a1fd95-4c6d-43a6-bb31-4ee8d5a44a8b       []         []          []   
1      6ff650ca-94ed-4119-8123-b113f9cc9957       []         []          []   
2      d0000ec2-2343-415b-ba58-6c14d0b8007e       []         []          []   
3      42e9fa7c-a981-44f9-943c-bf39a8c6ce8d       []         []          []   
4      34e7351d-715d-4b20-a5d6-3c0bd717eb1d       []         []          []   
...                                     ...      ...        ...         ...   
62859  6b94062e-78a3-46e8-b861-d801dfe27376       []         []          []   
62860  5ffbe933-6531-486a-91ea-553ee9036cd8       []         []          []   
62861  f7362574-05ac-4c21-8196-26a09d6e5fe7       []         []          []   
62862  6bd7adb1-b8dd-4ee5-bbe8-788444556350       []         []          []   
62863  9558b3a1-4eb8-4e45-8397-aadb54e572b4       []         []          []   

      lyrics written at libretto written at revised at translated at  \
0                    []                  []         []            []   
1                    []                  []         []            []   
2                    []                  []         []            []   
3                    []                  []         []            []   
4                    []                  []         []            []   
...                 ...                 ...        ...           ...   
62859                []                  []         []            []   
62860                []                  []         []            []   
62861                []                  []         []            []   
62862                []                  []         []            []   
62863                []                  []         []            []   

      arranged at commissioned dedication  
0              []           []         []  
1              []           []         []  
2              []           []         []  
3              []           []         []  
4              []           []         []  
...           ...          ...        ...  
62859          []           []         []  
62860          []           []         []  
62861          []           []         []  
62862          []           []         []  
62863          []           []         []  

[62864 rows x 11 columns]

In [245]:
def replace_empty_lists_with_none(df):

    """Iterates through DataFrame and replaces empty lists with None."""
    for col in df.columns:
        df[col] = df[col].apply(lambda x: None if isinstance(x, list) and not x else x)
    return df

In [246]:
work = replace_empty_lists_with_none(df_work_values_only)

In [247]:
work

place_id premiere written at composed at  \
0      f9a1fd95-4c6d-43a6-bb31-4ee8d5a44a8b     None       None        None   
1      6ff650ca-94ed-4119-8123-b113f9cc9957     None       None        None   
2      d0000ec2-2343-415b-ba58-6c14d0b8007e     None       None        None   
3      42e9fa7c-a981-44f9-943c-bf39a8c6ce8d     None       None        None   
4      34e7351d-715d-4b20-a5d6-3c0bd717eb1d     None       None        None   
...                                     ...      ...        ...         ...   
62859  6b94062e-78a3-46e8-b861-d801dfe27376     None       None        None   
62860  5ffbe933-6531-486a-91ea-553ee9036cd8     None       None        None   
62861  f7362574-05ac-4c21-8196-26a09d6e5fe7     None       None        None   
62862  6bd7adb1-b8dd-4ee5-bbe8-788444556350     None       None        None   
62863  9558b3a1-4eb8-4e45-8397-aadb54e572b4     None       None        None   

      lyrics written at libretto written at revised at translated at  \
0                  None                None       None          None   
1                  None                None       None          None   
2                  None                None       None          None   
3                  None                None       None          None   
4                  None                None       None          None   
...                 ...                 ...        ...           ...   
62859              None                None       None          None   
62860              None                None       None          None   
62861              None                None       None          None   
62862              None                None       None          None   
62863              None                None       None          None   

      arranged at commissioned dedication  
0            None         None       None  
1            None         None       None  
2            None         None       None  
3            None         None       None  
4            None         None       None  
...           ...          ...        ...  
62859        None         None       None  
62860        None         None       None  
62861        None         None       None  
62862        None         None       None  
62863        None         None       None  

[62864 rows x 11 columns]

In [248]:
value_counts = work.count().reset_index()
value_counts.columns = ['Column Name', 'Count']
value_counts

Column Name  Count
0              place_id  62864
1              premiere    232
2            written at     31
3           composed at     44
4     lyrics written at      8
5   libretto written at      0
6            revised at      2
7         translated at      0
8           arranged at      3
9          commissioned     29
10           dedication      5

In [249]:
def binary_encode_relationships(rel_series):
    """Converts extracted relationship values to binary encoding."""
    return rel_series.notna().astype(int)

In [250]:
df_binary_encoded = work.apply(binary_encode_relationships)

In [251]:
df_final_binary = pd.concat([df[["place_id"]], df_binary_encoded], axis=1)

In [252]:
df_final_binary.columns

Index(['place_id', 'place_id', 'premiere', 'written at', 'composed at',
       'lyrics written at', 'libretto written at', 'revised at',
       'translated at', 'arranged at', 'commissioned', 'dedication'],
      dtype='object')

In [253]:
def drop_second(df, col_name):
    """Drops the second occurrence of a column while keeping the first."""
    col_indices = [i for i, col in enumerate(df.columns) if col == col_name]

    if len(col_indices) > 1:
        df = df.loc[:, ~df.columns.duplicated(keep="first")]  # Keeps first, drops duplicates

    return df

In [254]:
df_final_binary = drop_second(df_final_binary, 'place_id')

In [255]:
df_final_binary

place_id  premiere  written at  \
0      f9a1fd95-4c6d-43a6-bb31-4ee8d5a44a8b         0           0   
1      6ff650ca-94ed-4119-8123-b113f9cc9957         0           0   
2      d0000ec2-2343-415b-ba58-6c14d0b8007e         0           0   
3      42e9fa7c-a981-44f9-943c-bf39a8c6ce8d         0           0   
4      34e7351d-715d-4b20-a5d6-3c0bd717eb1d         0           0   
...                                     ...       ...         ...   
62859  6b94062e-78a3-46e8-b861-d801dfe27376         0           0   
62860  5ffbe933-6531-486a-91ea-553ee9036cd8         0           0   
62861  f7362574-05ac-4c21-8196-26a09d6e5fe7         0           0   
62862  6bd7adb1-b8dd-4ee5-bbe8-788444556350         0           0   
62863  9558b3a1-4eb8-4e45-8397-aadb54e572b4         0           0   

       composed at  lyrics written at  libretto written at  revised at  \
0                0                  0                    0           0   
1                0                  0                    0           0   
2                0                  0                    0           0   
3                0                  0                    0           0   
4                0                  0                    0           0   
...            ...                ...                  ...         ...   
62859            0                  0                    0           0   
62860            0                  0                    0           0   
62861            0                  0                    0           0   
62862            0                  0                    0           0   
62863            0                  0                    0           0   

       translated at  arranged at  commissioned  dedication  
0                  0            0             0           0  
1                  0            0             0           0  
2                  0            0             0           0  
3                  0            0             0           0  
4                  0            0             0           0  
...              ...          ...           ...         ...  
62859              0            0             0           0  
62860              0            0             0           0  
62861              0            0             0           0  
62862              0            0             0           0  
62863              0            0             0           0  

[62864 rows x 11 columns]

In [256]:
df_final_binary.to_csv('place_work_binary.csv')

Place.csv Cleaning

In [357]:
df = pd.read_csv('places.csv')

In [358]:
df

id                     type  \
0      f9a1fd95-4c6d-43a6-bb31-4ee8d5a44a8b                   Studio   
1      6ff650ca-94ed-4119-8123-b113f9cc9957                   Studio   
2      d0000ec2-2343-415b-ba58-6c14d0b8007e                    Venue   
3      42e9fa7c-a981-44f9-943c-bf39a8c6ce8d                    Venue   
4      34e7351d-715d-4b20-a5d6-3c0bd717eb1d       Religious building   
...                                     ...                      ...   
69658  6b94062e-78a3-46e8-b861-d801dfe27376                   Studio   
69659  5ffbe933-6531-486a-91ea-553ee9036cd8                    Venue   
69660  f7362574-05ac-4c21-8196-26a09d6e5fe7                   Studio   
69661  6bd7adb1-b8dd-4ee5-bbe8-788444556350                   Studio   
69662  9558b3a1-4eb8-4e45-8397-aadb54e572b4  Educational institution   

                                    type-id  score  \
0      05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
1      05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
2      cd92781a-a73f-30e8-a430-55d7521338db    100   
3      cd92781a-a73f-30e8-a430-55d7521338db    100   
4      a120ca4a-69e9-3c0e-bc09-21cae26eb621    100   
...                                     ...    ...   
69658  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
69659  cd92781a-a73f-30e8-a430-55d7521338db    100   
69660  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
69661  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
69662  882d46c9-625c-4061-891c-22dd412744db    100   

                                             name  \
0                       Columbia (CBS) Studio ‘B’   
1                                Headroom Studios   
2                                   The Left Foot   
3                              New Theatre Oxford   
4      Santuario della Beata Vergine di Ariadello   
...                                           ...   
69658                               Studio Toupie   
69659                              名古屋BOTTOM LINE   
69660                               FatCat Studio   
69661                               Farida Studio   
69662   Community Consolidated School District 15   

                                                 address  \
0          49 East 52nd Street, Manhattan, New York City   
1               2026 E Hagert St, Philadelphia, PA 19125   
2              37 Throckmorton Street, Freehold, NJ, USA   
3                              George St, Oxford OX1 2AG   
4                                                    NaN   
...                                                  ...   
69658                                                NaN   
69659                       〒464-0850 愛知県名古屋市千種区今池4-7-11   
69660                                                NaN   
69661  FARIDA STUDIO, Lintel 17, 27711 Osterholz-Scha...   
69662                                                NaN   

                                             coordinates  \
0      {'latitude': '40.759164', 'longitude': '-73.97...   
1                                                    NaN   
2                                                    NaN   
3      {'latitude': '51.753951', 'longitude': '-1.260...   
4      {'latitude': '45.316087', 'longitude': '9.8651...   
...                                                  ...   
69658                                                NaN   
69659  {'latitude': '35.170066', 'longitude': '136.93...   
69660                                                NaN   
69661                                                NaN   
69662  {'latitude': '42.120748', 'longitude': '-88.11...   

                                                    area  \
0      {'id': '74e50e58-5deb-4b99-93a2-decbb365c07f',...   
1      {'id': '0eeb01c2-6e31-46ad-96b8-319749f731d2',...   
2      {'id': '42f86940-0f68-4ce0-8876-d070d424d91c',...   
3      {'id': '33587495-c775-4483-b819-931c4cf438cd',...   
4      {'id': '686e7b1e-613f-419c-bcc1-1e84df36586a',...   
...                                                  ...   
69658                       

In [359]:
import numpy as np
from scipy.spatial import cKDTree
import ast
from datetime import datetime

In [360]:
def extract_coordinates(coord_str):
    try:
        if pd.isna(coord_str) or not isinstance(coord_str, str):
            return np.nan, np.nan
        coord_dict = ast.literal_eval(coord_str.strip())
        return float(coord_dict["latitude"]), float(coord_dict["longitude"])
    except Exception as e:
        print(f"Error processing coordinates: {coord_str} -> {e}")
        return np.nan, np.nan


In [361]:
df[["latitude", "longitude"]] = df["coordinates"].apply(lambda x: pd.Series(extract_coordinates(x)))

In [362]:
df_missing_coords = df[df["latitude"].isna() | df["longitude"].isna()].copy()

In [363]:
df_valid_coords = df.dropna(subset=["latitude", "longitude"]).copy()

In [364]:
geo_cols = ["geonameid", "name", "asciiname", "alternatenames", "latitude", "longitude", "feature class",
            "feature code", "country code", "cc2", "admin1 code", "admin2 code", "admin3 code", "admin4 code",
            "population", "elevation", "dem", "timezone", "modification date"]

In [365]:
geo_data = pd.read_csv("allCountries.txt", sep="\t", header=None, names=geo_cols, usecols=["name", "latitude", "longitude", "country code", "admin1 code", "admin2 code"])


C:\Users\Vashist\AppData\Local\Temp\ipykernel_7204\1098501251.py:1: DtypeWarning: Columns (10,11) have mixed types. Specify dtype option on import or set low_memory=False.
  geo_data = pd.read_csv("allCountries.txt", sep="\t", header=None, names=geo_cols, usecols=["name", "latitude", "longitude", "country code", "admin1 code", "admin2 code"])


In [366]:
geo_data["latitude"] = pd.to_numeric(geo_data["latitude"], errors="coerce")
geo_data["longitude"] = pd.to_numeric(geo_data["longitude"], errors="coerce")

In [367]:
geo_data.dropna(subset=["latitude", "longitude"], inplace=True)

In [368]:
geo_data.rename(columns={"name": "city", "country code": "country", "admin1 code": "state_code", "admin2 code": "county_code"}, inplace=True)

In [369]:
geo_data["state_code"] = geo_data["state_code"].fillna("").astype(str)
geo_data["county_code"] = geo_data["county_code"].fillna("").astype(str)


In [370]:
admin1_cols = ["code", "state_name"]
admin1_data = pd.read_csv("admin1CodesASCII.txt", sep="\t", header=None, names=admin1_cols, usecols=[0, 1])

In [371]:
admin2_cols = ["code", "county_name"]
admin2_data = pd.read_csv("admin2Codes.txt", sep="\t", header=None, names=admin2_cols, usecols=[0, 1])

In [372]:
admin1_data["code"] = admin1_data["code"].astype(str)
admin2_data["code"] = admin2_data["code"].astype(str)

In [373]:
geo_data["state_full"] = geo_data["country"] + "." + geo_data["state_code"]
geo_data = geo_data.merge(admin1_data, left_on="state_full", right_on="code", how="left").drop(columns=["state_full", "code"])

In [374]:
geo_data["county_full"] = geo_data["country"] + "." + geo_data["state_code"] + "." + geo_data["county_code"]
geo_data = geo_data.merge(admin2_data, left_on="county_full", right_on="code", how="left").drop(columns=["county_full", "code"])

In [375]:
geo_data.rename(columns={"state_name": "state", "county_name": "county"}, inplace=True)

In [376]:
geo_coords = geo_data[["latitude", "longitude"]].to_numpy()
df_coords = df_valid_coords[["latitude", "longitude"]].to_numpy()

In [377]:
if not np.isfinite(df_coords).all():
    raise ValueError("df_coords contains NaN or infinite values. Check for missing or malformed lat/lon data.")

In [378]:
tree = cKDTree(geo_coords)

In [379]:
_, nearest_indices = tree.query(df_coords, k=1)  # k=1 -> Find the closest match

In [380]:
df_valid_coords["city"] = geo_data.iloc[nearest_indices]["city"].values
df_valid_coords["state"] = geo_data.iloc[nearest_indices]["state"].values
df_valid_coords["county"] = geo_data.iloc[nearest_indices]["county"].values
df_valid_coords["country"] = geo_data.iloc[nearest_indices]["country"].values

In [381]:
df_missing_coords["city"] = np.nan
df_missing_coords["state"] = np.nan
df_missing_coords["county"] = np.nan
df_missing_coords["country"] = np.nan

In [382]:
df_final = pd.concat([df_valid_coords, df_missing_coords], ignore_index=True)

In [383]:
df_final

id                type  \
0      f9a1fd95-4c6d-43a6-bb31-4ee8d5a44a8b              Studio   
1      42e9fa7c-a981-44f9-943c-bf39a8c6ce8d               Venue   
2      34e7351d-715d-4b20-a5d6-3c0bd717eb1d  Religious building   
3      0ad32768-514b-410f-9d5a-40ebb0c3373c              Studio   
4      0b050655-48da-4be7-b5de-7a3ee7370b9e               Venue   
...                                     ...                 ...   
69658  8f544074-fecb-49af-a761-c6e8b35d8486              Studio   
69659  90f30083-88db-49a7-8ec1-06d9ca2aa065               Venue   
69660  6b94062e-78a3-46e8-b861-d801dfe27376              Studio   
69661  f7362574-05ac-4c21-8196-26a09d6e5fe7              Studio   
69662  6bd7adb1-b8dd-4ee5-bbe8-788444556350              Studio   

                                    type-id  score  \
0      05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
1      cd92781a-a73f-30e8-a430-55d7521338db    100   
2      a120ca4a-69e9-3c0e-bc09-21cae26eb621    100   
3      05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
4      cd92781a-a73f-30e8-a430-55d7521338db    100   
...                                     ...    ...   
69658  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
69659  cd92781a-a73f-30e8-a430-55d7521338db    100   
69660  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
69661  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
69662  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   

                                             name  \
0                       Columbia (CBS) Studio ‘B’   
1                              New Theatre Oxford   
2      Santuario della Beata Vergine di Ariadello   
3                                         ROKU-st   
4                                   Rätschenmühle   
...                                           ...   
69658                              Full and Empty   
69659                                       Plama   
69660                               Studio Toupie   
69661                               FatCat Studio   
69662                               Farida Studio   

                                                 address  \
0          49 East 52nd Street, Manhattan, New York City   
1                              George St, Oxford OX1 2AG   
2                                                    NaN   
3                   〒106-0032 東京都港区六本木 3-4-24 六本木足立ビルB1F   
4         Schlachthausstraße 22, 73312 Geislingen/Steige   
...                                                  ...   
69658                                                NaN   
69659                                                NaN   
69660                                                NaN   
69661                                                NaN   
69662  FARIDA STUDIO, Lintel 17, 27711 Osterholz-Scha...   

                                             coordinates  \
0      {'latitude': '40.759164', 'longitude': '-73.97...   
1      {'latitude': '51.753951', 'longitude': '-1.260...   
2      {'latitude': '45.316087', 'longitude': '9.8651...   
3      {'latitude': '35.664122', 'longitude': '139.72...   
4      {'latitude': '48.627518', 'longitude': '9.8256...   
...                                                  ...   
69658                                                NaN   
69659                                                NaN   
69660                                                NaN   
69661                                                NaN   
69662                                                NaN   

                                                    area  \
0      {'id': '74e50e58-5deb-4b99-93a2-decbb365c07f',...   
1      {'id': '33587495-c775-4483-b819-931c4cf438cd',...   
2      {'id': '686e7b1e-613f-419c-bcc1-1e84df36586a',...   
3      {'id': 'd9fd27ac-b36f-492b-b598-039ee0dd08c1',...   
4      {'id': '4518c94c-b6ee-40d0-b4b6-fc27b06fa011',...   
...                                                  ...   
69658  {'id': '29a709d8-0320-493e-8d0c-f2c386662b7f',...   
69659  {'id': '70cd6f66-9881

In [388]:
def calculate_lifespan(row):
    try:
        life_span = row.get("life-span", None)  # Get 'life-span' column value safely

        # If 'life-span' is missing or not a dictionary, return NaN
        if not isinstance(life_span, dict):
            return np.nan

        # If only {'ended': None} is present, return NaN
        if "ended" in life_span and life_span["ended"] is None and "begin" not in life_span:
            return np.nan

        # Extract 'begin' year if present
        begin = life_span.get("begin", None)
        if begin is None or not isinstance(begin, str):
            return np.nan  # If no valid 'begin' value, return NaN

        begin_year = int(begin[:4])  # Extract first 4 characters for year

        # Determine 'ended' year
        ended = life_span.get("ended", None)
        if ended is None or ended == "None":
            ended_year = datetime.today().year  # Use current year if no end date
        else:
            ended_year = int(ended[:4])  # Extract first 4 characters for year

        return ended_year - begin_year
    except Exception:
        return np.nan

In [391]:
df_final["life-span"] = df_final["life-span"].apply(lambda x: ast.literal_eval(x) if isinstance(x, str) else x)
df_final["lifespan_years"] = df_final.apply(calculate_lifespan, axis=1)

In [392]:
df_final

id                type  \
0      f9a1fd95-4c6d-43a6-bb31-4ee8d5a44a8b              Studio   
1      42e9fa7c-a981-44f9-943c-bf39a8c6ce8d               Venue   
2      34e7351d-715d-4b20-a5d6-3c0bd717eb1d  Religious building   
3      0ad32768-514b-410f-9d5a-40ebb0c3373c              Studio   
4      0b050655-48da-4be7-b5de-7a3ee7370b9e               Venue   
...                                     ...                 ...   
69658  8f544074-fecb-49af-a761-c6e8b35d8486              Studio   
69659  90f30083-88db-49a7-8ec1-06d9ca2aa065               Venue   
69660  6b94062e-78a3-46e8-b861-d801dfe27376              Studio   
69661  f7362574-05ac-4c21-8196-26a09d6e5fe7              Studio   
69662  6bd7adb1-b8dd-4ee5-bbe8-788444556350              Studio   

                                    type-id  score  \
0      05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
1      cd92781a-a73f-30e8-a430-55d7521338db    100   
2      a120ca4a-69e9-3c0e-bc09-21cae26eb621    100   
3      05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
4      cd92781a-a73f-30e8-a430-55d7521338db    100   
...                                     ...    ...   
69658  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
69659  cd92781a-a73f-30e8-a430-55d7521338db    100   
69660  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
69661  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   
69662  05fa6a09-ff92-3d34-bdbb-5141d3c24f38    100   

                                             name  \
0                       Columbia (CBS) Studio ‘B’   
1                              New Theatre Oxford   
2      Santuario della Beata Vergine di Ariadello   
3                                         ROKU-st   
4                                   Rätschenmühle   
...                                           ...   
69658                              Full and Empty   
69659                                       Plama   
69660                               Studio Toupie   
69661                               FatCat Studio   
69662                               Farida Studio   

                                                 address  \
0          49 East 52nd Street, Manhattan, New York City   
1                              George St, Oxford OX1 2AG   
2                                                    NaN   
3                   〒106-0032 東京都港区六本木 3-4-24 六本木足立ビルB1F   
4         Schlachthausstraße 22, 73312 Geislingen/Steige   
...                                                  ...   
69658                                                NaN   
69659                                                NaN   
69660                                                NaN   
69661                                                NaN   
69662  FARIDA STUDIO, Lintel 17, 27711 Osterholz-Scha...   

                                             coordinates  \
0      {'latitude': '40.759164', 'longitude': '-73.97...   
1      {'latitude': '51.753951', 'longitude': '-1.260...   
2      {'latitude': '45.316087', 'longitude': '9.8651...   
3      {'latitude': '35.664122', 'longitude': '139.72...   
4      {'latitude': '48.627518', 'longitude': '9.8256...   
...                                                  ...   
69658                                                NaN   
69659                                                NaN   
69660                                                NaN   
69661                                                NaN   
69662                                                NaN   

                                                    area  \
0      {'id': '74e50e58-5deb-4b99-93a2-decbb365c07f',...   
1      {'id': '33587495-c775-4483-b819-931c4cf438cd',...   
2      {'id': '686e7b1e-613f-419c-bcc1-1e84df36586a',...   
3      {'id': 'd9fd27ac-b36f-492b-b598-039ee0dd08c1',...   
4      {'id': '4518c94c-b6ee-40d0-b4b6-fc27b06fa011',...   
...                                                  ...   
69658  {'id': '29a709d8-0320-493e-8d0c-f2c386662b7f',...   
69659  {'id': '70cd6f66-9881

In [393]:
df_final.to_csv('places_cleaned.csv')